In [1]:
import requests
import time
from bs4 import BeautifulSoup
import csv
from collections import defaultdict
import json
import sqlite3
from sqlite3 import Error
from queue import Queue 

In [2]:
# terms_dict = defaultdict(list)
terms_list = []
appDictionary = {}
relatedSearchTerms = {}

In [3]:
def commaSeparated(term):
    result = "";
    if len(term.split(' ')) > 1:
        count = len(term.split(' '));
        i = 0;
        for word in term.split(' '):
            if i > 0:
                result = result + "+";
            result = result + word;
            i = i + 1;
        return result;
    else:
        return term;

In [4]:
#Class to store app details in object format
class AppDetails:
    def __init__(self, title, description, stars, appID, imageSource, developerName):
        self.title = title
        self.description = description
        self.stars = stars
        self.appID = appID
        self.imageSource = imageSource
        self.developerName = developerName
        
    def toString(application):
        return application.title + ", " + application.appID + ", " + application.description + ", " + application.stars + ", " + application.imageSource + ", " + application.developerName

In [5]:
#DB DRIVERS

def create_connection(db_file):
    """ create a database connection to the SQLite database
        specified by db_file
    :param db_file: database file
    :return: Connection object or None
    """
    conn = None
    try:
        conn = sqlite3.connect(db_file)
        return conn
    except Error as e:
        print(e)
 
    return conn
            
            
def create_table(conn, create_table_sql):
    """ create a table from the create_table_sql statement
    :param conn: Connection object
    :param create_table_sql: a CREATE TABLE statement
    :return:
    """
    try:
        c = conn.cursor()
        c.execute(create_table_sql)
    except Error as e:
        print(e)
        
sql_create_appDetailsMainTable_table = """ CREATE TABLE IF NOT EXISTS appDetailsMainTable (
                                        key text NOT NULL,
                                        appIDs text NOT NULL,
                                        relatedSearchTerms text,
                                        source text NOT NULL
                                    ); """

sql_create_appDetails_table = """ CREATE TABLE IF NOT EXISTS appDetails (
                                        appID text NOT NULL,
                                        title text NOT NULL,
                                        description text,
                                        stars text,
                                        imageSource text,
                                        developerName text,
                                        source text
                                    ); """

sql_create_relatedSearchTerms_table = """ CREATE TABLE IF NOT EXISTS relatedSearchTerms (
                                        keyTerm text PRIMARY KEY,
                                        terms text NOT NULL,
                                        source text
                                    ); """

def databaseStartUp():
    # Create connection
    conn = create_connection(r"apkgk_database.db")

    # Create table
    if conn is not None:
        create_table(conn, sql_create_appDetailsMainTable_table)
        create_table(conn, sql_create_appDetails_table)
        create_table(conn, sql_create_relatedSearchTerms_table)
        print("Database created!")
    else:
        print("Error! cannot create the database connection.")
    
    return conn;
        
        
def insertIntoAppDetailsMainTable(conn, task):
 
    sql = ''' INSERT INTO appDetailsMainTable(key,appIDs,relatedSearchTerms,source)
              VALUES(?,?,?,?) '''
    cur = conn.cursor()
    cur.execute(sql, task)
    conn.commit()
    return cur.lastrowid

def insertIntoAppDetails(conn, task):
 
    sql = ''' INSERT INTO appDetails(appID, title, description, stars, imageSource, developerName, source)
              VALUES(?,?,?,?,?,?,?) '''
    cur = conn.cursor()
    cur.execute(sql, task)
    conn.commit()
    return cur.lastrowid
     
conn = databaseStartUp()

Database created!


In [6]:
with open('android_terms.csv','rt')as f:
  data = csv.reader(f)
  lineNumber = 0;
  for row in data:
        if lineNumber >= 1:
            key = row[2];
            terms = row[3];
            i = 0;
            for term in terms.split('"'):
                if i%2 == 0:
                    i = i+1;
                    continue
                else:
                    i = i+1;
                    terms_list.append(term)
        else:
            lineNumber = lineNumber + 1;

In [7]:
finalTermsList = []

In [8]:
finalTermsList.clear()
for term in terms_list:
    result = commaSeparated(term)
    finalTermsList.append(result)

In [9]:
len(finalTermsList)

432331

In [7]:
payload = {'q': 'mspy', 't': 'app'}
r = requests.get('https://apk.support/search', params=payload);
print(r.url)
print(r.status_code)

https://apk.support/search?q=mspy&t=app


In [9]:
# TEST
soup = BeautifulSoup(r.text, 'html.parser')
app_table = soup.find_all("h3")
appNamesList = []
for app in app_table:
    appName = app.get_text()
    appNamesList.append(appName)
appDictionary["mspy"] = appNamesList

In [ ]:
# TEST Cleanup List
for term in finalTermsList:
    if(term == ""):
        finalTermsList.remove(term)
singleWordSet = set();
for term in finalTermsList:
    if(term.find("+") == -1 and term != ""):
        singleWordSet.add(term)

In [10]:
q = Queue();
wordSet = set();
for term in finalTermsList:
    if(term != ""):
        wordSet.add(term)
print(len(wordSet))
for word in wordSet:
    q.put(word)
print(q.qsize())

1557
1557


In [70]:
# FOR TEST PURPOSE
singleWordSet = {'cheater', 'cheaters', 'cheating', 'track husband', 'keylogger', 'keyloggers'}

In [23]:
numberOfTerms = 0
while(q.empty() != True):
    word = q.get()
    time.sleep(1)
    print("Starting " + word + " " + str(numberOfTerms) + " with queue length " + str(q.qsize()))
    payload = {'q': word, 't': 'app'};
    r = requests.get('https://apk.support/search', params=payload);
    soup = BeautifulSoup(r.text, 'html.parser');
    # Get App Names
    names_table = soup.find_all("div", attrs={"class": "it_column"})
    if(len(names_table) == 0):
        print("Skipping " + word)
        continue
    finalList = []
    appIDList = ""
    first = 0
    for name in names_table:
        # Developer Information
        developerPart = name.find_all("div", attrs={"class": "ss_tg"})
        developerPart = developerPart[0].find_all("a")
        developerTag = developerPart[0]['href']
        developerTag = developerTag[10:]
        developerName = developerPart[0].get_text()
        information = name.find_all("a")
        # Title
        titleTag = information[0].find_all("h3")
        title = titleTag[0].get_text()
#         print("Title is " + title)
        # Description
        descriptionTag = information[0].find_all("p")
        description = descriptionTag[0].get_text()
#         print("Description is " + description)
        # Stars
        starsTag = information[0].find_all("div", attrs = {"class" : "stars"})
        starsSpan = starsTag[0].find_all("span")
        stars = starsSpan[0]['title']
        starCount = stars[stars.rindex(' ')+1:]
#         print("Stars is " + starCount)
        # AppID
        appID = information[0]['href']
        appID = appID[4 : ]
        if first != 0:
            appIDList = appIDList + ","
        appIDList = appIDList + appID
        first = 1
#         print("AppID:- " + appID)
        # Image Source Link
        imageTag = information[0].find_all("div", attrs={"class" : "seo_img"})
        imageTag = imageTag[0].find_all("img")
        imageSource = imageTag[0]['data-original']
#         print(" ImageSrc:- " + imageSource)
        perAppObject = AppDetails(title, description, starCount, appID, imageSource, developerName)
        
        # Insert Into App Table
        taskAppTable = (appID, title, description, stars, imageSource, developerName, 'apk.support');
        insertIntoAppDetails(conn, taskAppTable)
        
        finalList.append(perAppObject)
        
    # Suggestion Addition
    suggestionList = soup.find_all("div", attrs={"class": "suggest"})
    suggestionList = suggestionList[0].find_all("li")
    suggestions = []
    suggestionsString = "";
    i = 0
    for suggestion in suggestionList:
        suggestionName = suggestion.get_text()
        if (i != 0):
            suggestionsString = suggestionsString + ","
        suggestionsString = suggestionsString + suggestionName
        i = 1
        suggestions.append(suggestionName)
        modifiedSuggestionName = commaSeparated(suggestionName)
        if(modifiedSuggestionName not in wordSet):
#             print("Added " + modifiedSuggestionName)
            wordSet.add(modifiedSuggestionName)
            q.put(modifiedSuggestionName)
#         else:
#             print("Not Adding " + modifiedSuggestionName)
    
    #Insert Into Main Table
    taskMainTable = (word, appIDList, suggestionsString, 'apk.support');
    insertIntoAppDetailsMainTable(conn, taskMainTable)
    
    
#     appDictionary[word] = finalList
#     relatedSearchTerms[word] = suggestions
    numberOfTerms = numberOfTerms + 1
    if(numberOfTerms == 5000):
        break
    print("Completed " + word)

Starting automatic+call+recorder+2017+full+version 0 with queue length 1487
Skipping automatic+call+recorder+2017+full+version
Starting free+call+and+sms+trackr 0 with queue length 1486
Completed free+call+and+sms+trackr
Starting call+and+sms+trackar 1 with queue length 1488
Completed call+and+sms+trackar
Starting call+recorder+automatic+call+recorder+automatic 2 with queue length 1490
Completed call+recorder+automatic+call+recorder+automatic
Starting free+apps+to+catch+cheaters 3 with queue length 1490
Completed free+apps+to+catch+cheaters
Starting call+recording+app+for+samsung+j7+pro 4 with queue length 1489


KeyboardInterrupt: 

In [12]:
#https://apkgk.com/
numberOfTerms = 0
while(q.empty() != True):
    word = q.get()
    time.sleep(1)
    print("Starting " + word + " " + str(numberOfTerms) + " with queue length " + str(q.qsize()))
    payload = {'keyword': word}
    r = requests.get('https://apkgk.com/search/', params=payload);
    soup = BeautifulSoup(r.text, 'html.parser');
    appId = soup.find_all("ul", attrs={"class":'topic-wrap'})
    if(len(appId) == 0):
        print("Skipping " + word)
        continue
    appId = appId[0].find_all("a")
    names_table = soup.find_all('div', attrs={"class":'topic-bg'})
    if(len(names_table) == 0):
        print("Skipping " + word)
        continue
    finalList = []
    appIDList = ""
    first = 0
    counter = 0
    for name in names_table:
        appName = name.find_all("div", attrs={"class": "topic-tip-name"})
        appDesc = name.find_all("div", attrs={"class": "topic-tip-description"})
        appSrcMain  = name.find_all("div", attrs={"class": "c-lz-load"})
        imageTag = appSrcMain[0].find_all("img")
        appLink = imageTag[0]['data-src']
        #for img in appSrcMain:
        print(appId[counter]['href'])
        print(appLink)
        print(appName[0].get_text())
        print(appDesc[0].get_text())
        
        appID = appId[counter]['href']
        if first != 0:
            appIDList = appIDList + ","
        appIDList = appIDList + appID
        first = 1
        imageSource = appLink
        description = appDesc[0].get_text()
        title = appName[0].get_text()
        starCount = "NULL"
        developerName = "NULL"
        perAppObject = AppDetails(title, description, starCount, appID, imageSource, developerName)
        
        # Insert Into App Table
        taskAppTable = (appID, title, description, starCount, imageSource, developerName, 'apkgk.com');
        insertIntoAppDetails(conn, taskAppTable)
        
        finalList.append(perAppObject)
        counter=counter+1
    #Insert Into Main Table
    suggestionsString = "NULL"
    taskMainTable = (word, appIDList, suggestionsString, 'apkgk.com');
    insertIntoAppDetailsMainTable(conn, taskMainTable)
        
        


Starting auto+call+record+app+2018 0 with queue length 448
/automaticcallrecorder.supersmarthd.phonesecurity.musicsound.safedevice
//lh3.googleusercontent.com/cdq4E4flCo44fqexZKHWpNx-Ss-mOvP9vA3iHn2PHoq_6PRHwyu3GdoayZNkw1uImA=w220
Automatic Call Recorder 2018 by Cord Stones Pro
Records all your calls automatically when you answer them.
/com.callrecord.auto
//lh3.googleusercontent.com/yXKkk2PerSq8qWQoXOfWyPSDRB4TEn34RulFX-rV5xuf_EncATlhwWi8tEI0-2qUkWI=w220
Automatic Call Recorder
Automatic call recorder, best call recorder, phone call recorder
/com.skud.callrecorder.aleister
//lh3.googleusercontent.com/XWWYJGWBnVWsl9YVYShwg74E97ECDSlVGkFV2HEJyd3v1FNypIEQVUAQ9FI4HvNJmwQ=w220
Call Recorder 2018 by DarkWorld
Call Recorder 2018 - Record incoming call and outgoing call
/com.kachifhom.applegalmiro
//lh3.googleusercontent.com/3FuewnLYYsfkZ1aBqDn1PXathH5SwqzbpplhpF1v9cNJqC_6s-g2opeUUzdSLHoB7QKg=w220
kachifhom 2 - Calls Recorder Auto & Smart 2018
kachifhom 2 - Calls Recorder Auto & Smart 2018
/o

Starting automatic+call+recorder+for+samsung+note+8 0 with queue length 447
/com.smsrobot.callrecorder
//lh3.googleusercontent.com/ymWEjzLKpHdxkWhf90DS0SsEF-V9UgrB00k85UZDv-uGFGGaLtfQPNP6ytc5zmBmEQ=w220
Call Recorder - Automatic Call Recorder - callX
automatic call recorder, best call recorder,auto phone call recorder for android
/caller.live.freeapps.callrecorder
//lh3.googleusercontent.com/WMphQnmfcMbnaZW14MFQAQNLUBgBRCGoOFqFhER1NfFKP7mpReOZ1Vqy4RQPhFfMhBQh=w220
Call Recorder - Automatic Call Recorder (NO-ROOT)
High-quality automatic call recording free for Android, two-sided call recorder.
/com.killermobile.totalrecall.s2.trial
//lh3.googleusercontent.com/Zs_59ySxozMAdZs7xWTbQL4fVSPYiO7o8YTiHMUsk5EVtSPsMnhrLmu8OaL8oIjYX-hF=w220
Call Recorder S9 & S10
The #1 Call Recorder for your Samsung Galaxy S9 & S10 as well as Galaxy Note 9
/com.skud.callrecorder.aleister
//lh3.googleusercontent.com/XWWYJGWBnVWsl9YVYShwg74E97ECDSlVGkFV2HEJyd3v1FNypIEQVUAQ9FI4HvNJmwQ=w220
Call Recorder 2018 by Da

Starting auto+call+recorder+app+pro 0 with queue length 446
/com.smsrobot.callbox
//lh3.googleusercontent.com/FD-BLSjoGu44pm0mgIniFzCm5YDe1oE_pn2SnK9azJyQJ53IynoVSdv_dr4u3xH2Kg=w220
Automatic Call Recorder & Hide App Pro - callBOX
call recorder automatic, auto call recorder, hide apps icon, phone recorder
/com.appstar.callrecorderpro
//lh3.googleusercontent.com/of1YuQwfQCv9rysAv58hwb_7fTOBItBPXXrrnTLgIg7nyhv1EQdWgLMCZYV-_iAarUFB=w220
Automatic Call Recorder Pro
The best way to record your phone calls.
/com.superrecorder.callrec
//lh3.googleusercontent.com/yTU_ld3URvHPF3vQBzmMcHO2nm4tEgTTCEsLN5RjP5sZ8XBayFSltrwj9uOLSB8xqVmV=w220
Call Recorder & Hide App Pro Full voice clarity
call recorder automatic, auto call recorder, hide apps icon, phone recorder
/com.nzstudio.callrecorder
//lh3.googleusercontent.com/8O9u5P3CFUQ7DWZtrAhVPm2EuZY3gNxehM6O5WOEUu5EDNAfvYIFFGihcHibIYFXROU=w220
Automatic Call Recorder Pro by NZ Studio
Android Pro Automatic Call Recorder Free for all android users.
/phone.

Starting catch+him+cheating+get+his+text 0 with queue length 445
/com.ysdevloper.cheatinglover
//lh3.googleusercontent.com/g4rDjdGfW2oBy5rlWWcI5UIZfrC7Y8HWf9dFyNw3dXsQj-FIzsfG8j02Wz5TEKLGOLY=w220
catch a cheating LOVER by ys devloper
With the help of this app, u can know how to catch acheating lovrr easily.
/catch.a.cheating.lover
//lh3.googleusercontent.com/fwWup8MjdI3Yi1hN94c9AeHNck-84EJeE1dN-myodd1brULmXUU6eDvBSCe29sf7jQ=w220
CATCH A CHEATING LOVER
Catch a cheating lover easily with the help of this app. Includes tips, tricks .
/com.sumo.catchacheatinglover
//lh3.googleusercontent.com/LFE5vPm9R0_7Xgo0rivAopfY_Va_I04mbzbv_G7LMplzFoSRkDpvG_ZirDgX0DGsj98=w220
Catch A Cheating Lover
Learn to Catch A Cheating Lover Without Them Knowing
/com.taptap.cheating
//lh3.googleusercontent.com/I5cGRNLFktpwgtrW-rUqN10NPpOfmzLhIOyE4GsdiV4dZIwMivPCJrejJ8KLlE1qOTI=w220
Catch Your Cheating Spouse!
Do you suspect someone is cheating on you? Do you want to bust ‘em in the act?
/com.andromo.dev499681.app5

Starting automatic+call+recorder+&+hide+app+pro+-+callbox 0 with queue length 444
/com.smsrobot.callbox
//lh3.googleusercontent.com/FD-BLSjoGu44pm0mgIniFzCm5YDe1oE_pn2SnK9azJyQJ53IynoVSdv_dr4u3xH2Kg=w220
Automatic Call Recorder & Hide App Pro - callBOX
call recorder automatic, auto call recorder, hide apps icon, phone recorder
/com.smsrobot.call.recorder.callsbox
//lh3.googleusercontent.com/rSN_NLoUq3AWd17TxL0l45MifJdMYuK0tZHUsMqrKNaQX-cOg8DzHiKT2E2fGhwDtNva=w220
Automatic Call Recorder - CallsBOX
call recorder automatic, best call recorder,auto phone call recorder for android
/com.arithmatrix.callrecorder.advertisement
//lh3.googleusercontent.com/LjSMJjubMYFpGGbyzzCqQszHaUmsHWWZmNtV3xfxqXTZ_TrDuQbm1X7f1w9wSeHVJNk=w220
Call Recorder 2020
Call Recording | Call Recorder | Auto Call Recording | Phone Recorder
/com.smsrobot.callrecorder
//lh3.googleusercontent.com/ymWEjzLKpHdxkWhf90DS0SsEF-V9UgrB00k85UZDv-uGFGGaLtfQPNP6ytc5zmBmEQ=w220
Call Recorder - Automatic Call Recorder - callX
automat

...

/com.mobile.numberlocation.phone.calls.numbertracker
//lh3.googleusercontent.com/FKpnv6-jUnG3qogB3w3zurU4pUVv6BoI4dg9hBPJZJYTU1SAbkoAqyMl3EipMp3FWl_v=w220
Number Locator - Mobile Caller Location
Mobile Number Locator - Caller Location, Find Phone Numbers, STD & ISD Codes
/livemobilelocationtracker.teccreations
//lh3.googleusercontent.com/6XFhCdQAHqXu8VnSDE9vpvXO0wq1IrPvii4g5GnbuvvLZlxJzPZN5HjxxS6upu9-Ug=w220
Live Mobile Location and GPS Coordinates
Live Mobile Location is a Wonderful app to find their Current location
/com.mspy.lite
//lh3.googleusercontent.com/GhfDb8k21PcJoqeRLAQWqtdfKZ4jOoqFsL6hdjBLSom8LG1KA-ORIQKmdqJuU2NBTgBy=w220
mLite Family Phone Tracker, GPS Location App
Parental Control, Find my Child's and Family Members Location
/com.droid.caller.id.phone.number.location
//lh3.googleusercontent.com/U1TxGRVoD0YDkMjwTUPzP389nird4A-p_3igsEif4BsJ02XCvlIAxTCxgXf9QQBK-sU=w220
Caller ID & Number Locator
Mobile Number Locator, caller ID, call blocker.
/com.sri.mobilenumberlocator
//lh

/com.enlightment.voicecallrecorder
//lh3.googleusercontent.com/2dpPxFxKvNYAbO2ShEg_KqXtXqfZGNZeXFNkflq_z-wlP2FECFclxq3B0qPBh_WKAQ=w220
Call Recorder
Best tool for recording your phone calls.
/com.callrecorderautomatic.acrcallrecording
//lh3.googleusercontent.com/GFSxZSM0vengNtJYorDsiDHSwZV-hqhDDYzooUhIp8X9YQFng8X-WJSXLN55acBxU4Y=w220
Call Recorder - Automation Call Recording, 2 Ways
Auto call recorder incoming and outgoing, best call recording
/com.creativeappinc.autocallrecorder
//lh3.googleusercontent.com/z4ZKV-y4pZjyVHvCXD6IiRY_V9Qx9j4zh3I_CNoIdRcBWXiNkHupgBj6vLOIVIhTPQ=w220
Auto Call Recorder : Hide App
Auto Call Recorder : Hide App
/phone.automatic.call.recorder.arc
//lh3.googleusercontent.com/ipczYcfgqVPagqDd5-_6U7ZdOX7oRv94vjfjQftNiVQlxnpA2fpz2iMHLVhdjIXKWXEP=w220
Automatic Call Recorder Pro - Recorder Phone Call
Automatic Call Recorder is app the record phone conversation, block spam calls.
/com.appscorner.callrecorde
//lh3.googleusercontent.com/B_-4Tl5hPMj9m1KppIXMoWmj4XnEPxXr

/com.fsp.android.friendlocator
//lh3.googleusercontent.com/OqsZe2Rypm2Q8gIvlKHE3Gr0K232g2SRozwE0YS_iYCgPScfMKWa9Aw-fua532wCUA=w220
Find My Friends
Share your location with your friends for FREE
/com.cellnumbertracker.phone
//lh3.googleusercontent.com/yNa6he63yurvdrMNd7ebn4p5zoaYTuJcJnDIl8JbaXiJT1MPhOhTDk6yCN2vRqP4Guc=w220
Phone Number Tracker
Lookup specific phone numbers. Name From Number. Accurate Caller ID. Love caller
/com.appsmartplus.gpsmobilelocationtracker.route.finder
//lh3.googleusercontent.com/RyDhuABjgJPTs7CsygBcwFiQj1FgvusgDUw7t0xgltWf3rIyvvW27f_9StPsaMrb8g=w220
Mobile Number Location GPS
Do you want to be constantly updated by current location
/com.securellc.phone.tracker.caller
//lh3.googleusercontent.com/k_vBohHBc-ca0OpCnlhEpJ3eM1WZ_GhvV3V1h9q-1s4Ktu4cduEEyj6HAGSysCVzWA=w220
Mobile Tracker In English
Free mobile tracker in English with only phone number 📲
/com.isharing.isharing
//lh3.googleusercontent.com/0Vwwrd5cl0ZyNS6qQp2VlgJqPBFFtNMZv-QkUTai5tUWSBmkmBGZwPh0-tYx9Us7i

/com.appsmartplus.gpsmobilelocationtracker.route.finder
//lh3.googleusercontent.com/RyDhuABjgJPTs7CsygBcwFiQj1FgvusgDUw7t0xgltWf3rIyvvW27f_9StPsaMrb8g=w220
Mobile Number Location GPS
Do you want to be constantly updated by current location
/com.sri.mobilenumberlocator
//lh3.googleusercontent.com/E6fDwIOsccgjnEMVcbC254XDLUQES7eYDWOhNTONgXNtcpKXIiS_jFOzcZzVOCUPe3Y=w220
Mobile Number Locator
Mobile Number Locator, Caller Location Tracker - Block Calls, Phone Call Screen
/com.aappstech.flpmaps
//lh3.googleusercontent.com/uiOAceZScIL2JcGc5o3RTbaf3qm8ePmP-gEUYkIjcTuKRX-zAXz9A38fCqS4i0FoQA=w220
Find My Phone: Find Lost Phone
Find My Phone finds your lost phone in seconds, It also find lost phone
/org.findmykids.app
//lh3.googleusercontent.com/FvOqyZd0ljreG4TTddFagvi2a7BxyTAX648X_IuajT8f4Z62C7DJjdmHqMAzZ8_Hfw=w220
Find My Kids: Child Cell Phone Tracker & GPS-watch
Editor's choice! Child GPS tracker. Locate kids on the map online. Sound around.
/com.wavemarket.finder.mobile
//lh3.googleusercont

/com.nav.mobile.tracker
//lh3.googleusercontent.com/jwghbMiEPxipQoRVxdDCnWEPebbcYPrU841thUUzoKhFOf5GvbLkWD7B_PS6G8g_ivXa=w220
Mobile Tracker for Android
Track your lost mobile. Get location address. Get details of any mobile number.
/com.newatifapps1.mobilegpslocationfind.gpslocationtravker.findmyphone
//lh3.googleusercontent.com/wIotYG5WznmALbdi4zkD0TjXC5FkOL8TaNGmptM8Ppqz5w2Dhl4cu7wZLVHTJelY3n-z=w220
GPS Mobile Number Location Finder:Travel Together
GPS Mobile Number Location Finder is a GPS type app,that find mobile with GPS.
/us.B3S.NumberLocator
//lh3.googleusercontent.com/9zMurXwUcX2m4o3jLhITX3CTD_M0XMPORgDgp9rP4hAwZXmM_ffw0L9UlWIguKm1_Byo=w220
Check phone number location
Enter phone number prefix and check country of the caller
/com.fsp.android.c
//lh3.googleusercontent.com/WZdtOpMJFXAOMJuKsGi3dhchRj55xRIIQaro3wI8DeDUyJ2VdeeaA8JJkvG2y9OM5baK=w220
GPS Phone Tracker
Never lose your phone again
/com.truthfinderphone.app
//lh3.googleusercontent.com/xfQced9sSm4gdARe3VFiOiycBJ_vjNNRGN

In [ ]:
# Map check Code
for app in appDictionary:
    appList = appDictionary[app]
    print("Entries for " + app)
    for application in appList:
        print(application.toString())
        print("------------------------------->>>")

In [ ]:
# Saving dict to file
with open('apksupport.json', 'w') as f:
    json.dump(appDictionary, f)

with open('relatedSearchTerms_apksupport.json', 'w') as f:
    json.dump(relatedSearchTerms, f)

In [ ]:
SQLite3
dataset package python

upper table -> key and set of app ids
lower table -> app id is primary key and we write to this.

In [15]:
conn.close()